In [1]:
using Plots, LinearAlgebra

In [2]:
m  = 1 
w  = 1
ws = 2
g  = 1.5
g1 = g
g2 = g
lamda  = 2

2

In [3]:
function H_s(x,p)
    sigma_z = [1 0; 0 -1]
    hs = (ws/2) * ( kron(sigma_z,I(2)) + kron(I(2),sigma_z) )
    sigma_plus  = [0 1;0 0]
    sigma_minus = [0 0;1 0]
    a       = x*sqrt(m*w/2) + im*p/sqrt(m*w*2)
    hos     = (g1/2) * ( kron(a*sigma_plus + conj(a)*sigma_minus,I(2)) ) + ( kron(I(2), (g2/2)*(a*sigma_plus + conj(a)*sigma_minus) ))
    hss = (lamda/2) * (kron(sigma_plus,sigma_minus) + kron(sigma_minus,sigma_plus))
return hs+hos+hss
end

function H_t(x,p)
    ho = ( p^2/(2*m) + (1/2)*m*w^2*x^2 ) * ( kron(I(2),I(2)) )
return ho+H_s(x,p)
end

function H_eff(x,p,psi)
    return real(psi'*H_t(x,p)*psi)
end


function Entropy(psi)
    rho = psi*psi'
    a = rho[1,1]+rho[2,2]
    b = rho[3,3]+rho[4,4]
    return -real((a*log(complex(a))+b*log(complex(b))))
end

Entropy (generic function with 1 method)

In [4]:
function run()    
    dt = 0.0001
    N  = 500000
    Nd = Int(0.001/dt)
    dp = 0.0001
    dx = 0.0001
    x0  = 0.1
    p0  = 0
    psi0  = [1;0;0;0]

    global xdata = zeros(Int(N/Nd))
    global pdata = zeros(Int(N/Nd))
    global Ess   = zeros(Int(N/Nd))
    global Eo    = zeros(Int(N/Nd))
    global Sent  = zeros(Int(N/Nd))
    global time  = zeros(Int(N/Nd))

    xdata[1] = x0 
    pdata[1] = p0
    Ess[1]   = real(psi0'*H_s(x0,p0)*psi0)
    Eo[1]    = p0^2/(2*m) + (1/2)*m*w^2*x0^2  
    Sent[1]  = Entropy(psi0)
    time[1]  = 0

    j = 2
    for i=2:N-1
        psi = ([1 0 0 0;0 1 0 0; 0 0 1 0; 0 0 0 1] - im.*H_s(x0,p0)*dt) * psi0
        x = x0 + ( ( H_eff(x0,p0+dp,psi0) - H_eff(x0,p0,psi0) )/(dp) ) * dt
        p = p0 - ( ( H_eff(x0+dx,p0,psi0) - H_eff(x0,p0,psi0) )/(dx) ) * dt

        if mod(i,Nd) ==0
            xdata[j] = x 
            pdata[j] = p 
            Ess[j] = real(psi'*H_s(x,p)*psi)
            Eo[j] = p^2/(2*m) + (1/2)*m*w^2*x^2 
            Sent[j]  = Entropy(psi)
            time[j]  = i*dt
            j = j+1
        end

        x0=x
        p0=p
        psi0=psi

    end 
    
end

@time run()

 19.069024 seconds (175.10 M allocations: 15.449 GiB, 11.67% gc time, 7.28% compilation time)


In [5]:
g=1.5
g1=g
g2=g
run()
l = @layout [a{0.5w};[grid(3,1)]]
p1=plot(xdata,pdata,title="Trajectory, g = $(g)",xlabel="x",ylabel="p",label="")
p2=plot(time,Ess,title="Spin Subsystem Energy",xlabel="t",ylabel="\$E_{ss}\$",ylim=(0,2.1),yticks=[0,1,2.1],label="")
p3=plot(time,Eo,title="Oscillator Energy Eo",xlabel="t",ylabel="\$E_o\$",ylim=(0,1.5),yticks=[0.0,0.75,1.5],label="")
p4=plot(time,Sent,title="Entanglement Entropy",xlabel="t",ylabel="\$S_{ent}\$",ylim=(0.0,0.8),yticks=[0.0,0.4,0.8],label="")
plt_SC1 = plot(p1,p2,p3,p4,layout = l,framestyle=:box,size = (900,1000))
display(plt_SC1)

In [6]:
g=0.1
g1=g
g2=g
run()
l = @layout [a{0.5w};[grid(3,1)]]
p1=plot(xdata,pdata,title="Trajectory, g = $(g)",xlabel="x",ylabel="p",label="")
p2=plot(time,Ess,title="Spin Subsystem Energy",xlabel="t",ylabel="\$E_{ss}\$",ylim=(1,2),yticks=[1,1.5,2],label="")
p3=plot(time,Eo,title="Oscillator Energy Eo",xlabel="t",ylabel="\$E_o\$",ylim=(0,1),yticks=[0,0.5,1],label="")
p4=plot(time,Sent,title="Entanglement Entropy",xlabel="t",ylabel="\$S_{ent}\$",ylim=(0,0.8),yticks=[0,0.4,0.8],label="")
plt_SC1 = plot(p1,p2,p3,p4,layout = l,framestyle=:box,size = (900,1000))
display(plt_SC1)

In [ ]:
g=0.0001
g1=g
g2=g
run()
l = @layout [a{0.5w};[grid(3,1)]]
p1=plot(xdata,pdata,title="Trajectory, g = $(g)",xlabel="x",ylabel="p",label="")
p2=plot(time,Ess,title="Spin Subsystem Energy",xlabel="t",ylabel="\$E_{ss}\$",ylim=(1.9,2.1),yticks=[1.9,2.0,2.1],label="")
p3=plot(time,Eo,title="Oscillator Energy Eo",xlabel="t",ylabel="\$E_o\$",ylim=(0.0025,0.007),yticks=[0.003,0.005,0.007],label="")
p4=plot(time,Sent,title="Entanglement Entropy",xlabel="t",ylabel="\$S_{ent}\$",ylim=(-0.1,0.1),yticks=[-0.1,0,0.1],label="")
plt_SC1 = plot(p1,p2,p3,p4,layout = l,framestyle=:box,size = (900,1000))
display(plt_SC1)